In [16]:
# boilerplate setup
import leafmap.maplibregl as leafmap
import ibis
from ibis import _

conn = ibis.duckdb.connect()
ca_parquet = "https://data.source.coop/cboettig/ca30x30/ca_areas.parquet"
# or use local copy:
ca_parquet = "/home/rstudio/source.coop/cboettig/ca30x30/ca_areas.parquet"


In [ ]:
# Visualize the full data to show overlap:
import leafmap.maplibregl as leafmap
ca_pmtiles = "https://data.source.coop/cboettig/ca30x30/ca_areas.pmtiles"
style = {
    "version": 8,
    "sources": {
        "ca": {
            "type": "vector",
            "url": "pmtiles://" + ca_pmtiles,
        }},
    "layers": [{
            "id": "layer1",
            "source": "ca",
            "source-layer": "CA_Cons_Areas_parentlyr_Merge_ecofix",
            "type": "fill",
            "filter": ["<",["get", "reGAP"], 3,],
            "paint": {
                "fill-color": {
            'property': 'Release_Year',
            'type': 'categorical',
            'stops': [[2023, "#FF000080"],  # note RGBA code includes alpha
                      [2024, "#0000FF80"]]
            },
                "fill-opacity": 0.5 # ignored? 
            }
        }]}

m = leafmap.Map(style="positron")
m.add_pmtiles(ca_pmtiles, style = style)
m.to_html("ca30x30_gap12.html") # save a copy
m


In [17]:
# Make things faster.  Let's zoom in on a subset of the data. 

from ibis.interactive import *
ca_parquet = "/home/rstudio/source.coop/cboettig/ca30x30/ca_areas.parquet"
conn = ibis.duckdb.connect()

# Ugly code for a cookie cutter zoom
# Turns out we could have just used filter(_.UNIT_NAME == "Angeles National Forest")
import geopandas as gpd
from shapely.geometry import box
min_lon, min_lat, max_lon, max_lat = -118.4, 34., -117.545715, 34.495239
bbox = box(min_lon, min_lat, max_lon, max_lat)
gdf = gpd.GeoDataFrame({'geometry': [bbox]}, crs="EPSG:4326")
cookie_cutter = ibis.literal(gdf.geometry.iloc[0])

angeles_forest = (
    conn.read_parquet(ca_parquet)
    .cast({"SHAPE": "geometry"})
    .rename(geom = "SHAPE")
 #   .mutate(geom = _.geom.convert("epsg:3310","epsg:4326"))
 #   .filter( _.geom.intersects(cookie_cutter))
 #   .filter(_.UNIT_NAME == "Angeles National Forest") 
    .select("reGAP", "UNIT_NAME", "MNG_AGNCY", "Release_Year", "OBJECTID", "geom")
)
# split 2023 & 2024
allgap_2023 = angeles_forest.filter(_.Release_Year == 2023)
allgap_2024 = angeles_forest.filter(_.Release_Year == 2024)

In [25]:
import ibis
from ibis import _
buffer = -0.0003 

tbl = (
    conn.read_parquet("https://data.source.coop/cboettig/ca30x30/ca_areas.parquet")
    .cast({"SHAPE": "geometry"})
    .rename(geom = "SHAPE")
  #  .filter(_.UNIT_NAME == "Angeles National Forest")
    .filter(_.reGAP < 3) 
    .mutate(geom = _.geom.convert("epsg:3310","epsg:4326"))
)
tbl_2023 = tbl.filter(_.Release_Year == 2023).mutate(geom=_.geom.buffer(buffer))
tbl_2024 = tbl.filter(_.Release_Year == 2024)
intersects = tbl_2024.anti_join(tbl_2023, _.geom.intersects(tbl_2023.geom))

In [27]:
new = intersects.execute()

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [28]:
new.to_parquet("new2024.parquet")

In [26]:
import leafmap.maplibregl as leafmap

release_year = {'property': 'Release_Year', 'type': 'categorical','stops': [[2023, "#FF000080"], [2024, "#0000FF80"]]},
gap = {
        'property': 'reGAP',
        'type': 'categorical',
        'stops': [
            [1, "#26633d"],
            [2, "#879647"],
            [3, "#BBBBBB"],
            [4, "#F8F8F8"]]
        }
paint = {"fill-color": gap, "fill-opacity": 0.5}

m = leafmap.Map(style="positron")
m.add_gdf(intersects.execute(),layer_type="fill", name = "intes", paint=paint)
m.add_layer_control()
m.to_html("new_in_2024.html")
m

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

Map(height='600px', map_options={'bearing': 0, 'center': (0, 20), 'pitch': 0, 'style': 'https://basemaps.carto…

Using difference (overlap) instead:

In [30]:
%%time
import duckdb
db = duckdb.connect()
db.install_extension("spatial")
db.load_extension("spatial")


tbl_2023 = tbl.filter(_.Release_Year == 2023) # no buffer
tbl_2024 = tbl.filter(_.Release_Year == 2024)
tbl_2023.execute().to_file("la_2023.geojson")
tbl_2024.execute().to_file("la_2024.geojson")


db.sql('''
CREATE OR REPLACE TABLE t1 AS SELECT OBJECTID AS gid, st_make_valid(geom) AS geom, FROM st_read("la_2024.geojson");
CREATE OR REPLACE TABLE t2 AS SELECT OBJECTID AS gid, st_make_valid(geom) AS geom, FROM st_read("la_2023.geojson");
''')
db.sql('''
COPY (
with temp as 
(
  select   b.gid, st_union_agg(a.geom) as geom
  from     t1 b join t2 a on st_intersects(a.geom, b.geom)
  group by b.gid
) 
select st_difference(b.geom,coalesce(t.geom, 'GEOMETRYCOLLECTION EMPTY'::geometry)) as geom
from t1 b left join temp t on b.gid = t.gid
) TO 'new2024.geojson' WITH (FORMAT GDAL, DRIVER 'GeoJSON', LAYER_CREATION_OPTIONS 'WRITE_BBOX=YES')
''')

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

InvalidInputException: Invalid Input Error: Attempting to execute an unsuccessful or closed pending query result
Error: Catalog Error: Scalar Function with name st_make_valid does not exist!
Did you mean "ST_MakeValid"?
LINE 2: ...ACE TABLE t1 AS SELECT OBJECTID AS gid, st_make_valid(geom) AS geom, FROM st_r...
                                                  ^

In [10]:
import ibis
from ibis import _
con = ibis.duckdb.connect()
diff = con.read_geo("new2024.geojson")


In [16]:
import leafmap.maplibregl as leafmap

m = leafmap.Map(style="positron")
m.add_gdf(diff.execute(),layer_type="fill", name = "diff", paint = {"fill-opacity": 0.5})
m.add_layer_control()
m


Map(height='600px', map_options={'bearing': 0, 'center': (0, 20), 'pitch': 0, 'style': 'https://basemaps.carto…

In [6]:
ca

r0 := DatabaseTable: ibis_read_parquet_3fotibldaretnd5wjeicmg4oli
  OBJECTID           int64
  cpad_ACCESS_TYP    string
  cpad_PARK_NAME     string
  cpad_MNG_AGENCY    string
  cpad_MNG_AG_LEV    string
  reGAP              int16
  Easement           int16
  TYPE               string
  CA_County_Name     string
  CA_Region_Name     string
  TerrMar            string
  CA_Ecoregion_Name  string
  ACCESS_TYP         string
  MNG_AGNCY          string
  MNG_AG_LEV         string
  UNIT_NAME          string
  DefaultSelection   string
  CA_Ecoregion_Acres float32
  CA_Region_Acres    float32
  CA_County_Acres    float32
  Acres              float32
  CA_Marine_Acres    float32
  Release_Year       int16
  mgmt_stack         string
  SHAPE              binary
  SHAPE_bbox         xmin: float32
  ymin: float32
  xmax: float32
  ymax: float32

r1 := DatabaseTable: ibis_read_parquet_t3lw66szfrfcrj34bcr6dbmi64
  OBJECTID           int64
  cpad_ACCESS_TYP    string
  cpad_PARK_NAME     string
  cpad_MNG_AGENCY    string
  cpad_MNG_AG_LEV    string
  reGAP              int16
  Easement           int16
  TYPE               string
  CA_County_Name     string
  CA_Region_Name     string
  TerrMar            string
  CA_Ecoregion_Name  string
  ACCESS_TYP         string
  MNG_AGNCY          string
  MNG_AG_LEV         string
  UNIT_NAME          string
  DefaultSelection   string
  CA_Ecoregion_Acres float32
  CA_Region_Acres    float32
  CA_County_Acres    float32
  Acres              float32
  CA_Marine_Acres    float32
  Release_Year       int16
  mgmt_stack         string
  geom               binary
  SHAPE_bbox         xmax: float64
  xmin: float64
  ymax: float64
  ymin: float64

r2 := Project[r1]
  OBJECTID: r1.OBJECTID

r3 := Project[r0]
  OBJECTID:           r0.OBJECTID
  cpad_ACCESS_TYP:    r0.cpad_ACCESS_TYP
  cpad_PARK_NAME:     r0.cpad_PARK_NAME
  cpad_MNG_AGENCY:    r0.cpad_MNG_AGENCY
  cpad_MNG_AG_LEV:    r0.cpad_MNG_AG_LEV
  reGAP:              r0.reGAP
  Easement:           r0.Easement
  TYPE:               r0.TYPE
  CA_County_Name:     r0.CA_County_Name
  CA_Region_Name:     r0.CA_Region_Name
  TerrMar:            r0.TerrMar
  CA_Ecoregion_Name:  r0.CA_Ecoregion_Name
  ACCESS_TYP:         r0.ACCESS_TYP
  MNG_AGNCY:          r0.MNG_AGNCY
  MNG_AG_LEV:         r0.MNG_AG_LEV
  UNIT_NAME:          r0.UNIT_NAME
  DefaultSelection:   r0.DefaultSelection
  CA_Ecoregion_Acres: r0.CA_Ecoregion_Acres
  CA_Region_Acres:    r0.CA_Region_Acres
  CA_County_Acres:    r0.CA_County_Acres
  Acres:              r0.Acres
  CA_Marine_Acres:    r0.CA_Marine_Acres
  Release_Year:       r0.Release_Year
  mgmt_stack:         r0.mgmt_stack
  SHAPE:              Cast(r0.SHAPE, to=geospatial:geometry)
  SHAPE_bbox:         r0.SHAPE_bbox

r4 := Project[r2]
  OBJECTID:    r2.OBJECTID
  established: 2024

r5 := Project[r3]
  OBJECTID:           r3.OBJECTID
  cpad_ACCESS_TYP:    r3.cpad_ACCESS_TYP
  cpad_PARK_NAME:     r3.cpad_PARK_NAME
  cpad_MNG_AGENCY:    r3.cpad_MNG_AGENCY
  cpad_MNG_AG_LEV:    r3.cpad_MNG_AG_LEV
  reGAP:              r3.reGAP
  Easement:           r3.Easement
  TYPE:               r3.TYPE
  CA_County_Name:     r3.CA_County_Name
  CA_Region_Name:     r3.CA_Region_Name
  TerrMar:            r3.TerrMar
  CA_Ecoregion_Name:  r3.CA_Ecoregion_Name
  ACCESS_TYP:         r3.ACCESS_TYP
  MNG_AGNCY:          r3.MNG_AGNCY
  MNG_AG_LEV:         r3.MNG_AG_LEV
  UNIT_NAME:          r3.UNIT_NAME
  DefaultSelection:   r3.DefaultSelection
  CA_Ecoregion_Acres: r3.CA_Ecoregion_Acres
  CA_Region_Acres:    r3.CA_Region_Acres
  CA_County_Acres:    r3.CA_County_Acres
  Acres:              r3.Acres
  CA_Marine_Acres:    r3.CA_Marine_Acres
  Release_Year:       r3.Release_Year
  mgmt_stack:         r3.mgmt_stack
  SHAPE:              r3.SHAPE
  SHAPE_bbox:         r3.SHAPE_bbox
  area:               GeoArea(r3.SHAPE)

r6 := JoinChain[r5]
  JoinLink[left, r4]
    r5.OBJECTID == r4.OBJECTID
  values:
    OBJECTID:           r5.OBJECTID
    cpad_ACCESS_TYP: 

In [27]:
import leafmap.maplibregl as leafmap
import ibis
from ibis import _
ca_parquet = "ca_areas.parquet"

con = ibis.duckdb.connect()
new2024 = (con
      .read_parquet("new2024.parquet")
      .select("OBJECTID")
      .mutate(established = 2024)
     )

ca = (con
      .read_parquet(ca_parquet)
      .cast({"SHAPE": "geometry"})
      .mutate(area = _.SHAPE.area())
      .filter(_.reGAP < 3)
      .left_join(new2024, "OBJECTID")
      .mutate(established=_.established.fill_null(2023))
      .mutate(geom = _.SHAPE.convert("epsg:3310","epsg:4326"))
      .rename(name = "UNIT_NAME", access_type = "ACCESS_TYP", manager = "MNG_AGNCY", manager_type = "MNG_AG_LEV", id = "OBJECTID")
      .select(_.established, _.reGAP, _.name, _.access_type, _.manager, _.manager_type, _.Easement, _.Acres, _.id,  _.geom)
     )


In [32]:
# compute some summary tables:
(ca
 .filter(_.established == 2024)
 .group_by(_.manager_type)
 .agg(area = _.Acres.sum())
 .order_by(_.area.desc())
 .execute()
)

manager_type           area
0                     Non Profit  458009.641083
1                        Federal  158633.082092
2                          State  106750.540298
3               Special District   94705.677739
4                         County   15834.462494
5                        Unknown    8292.326221
6                           City    2773.695034
7                        Private      42.579013
8        Home Owners Association      39.521428
9   Joint Powers Authority (JPA)      11.565516
10                    Government       4.377818
11              Local Government       0.029984

In [35]:
gdf = ca.filter(_.manager_type == "State").execute()

In [36]:
established = {'property': 'established',
               'type': 'categorical',
               'stops': [
                   [2023, "#26542C80"], 
                   [2024, "#F3AB3D80"]]
              }
gap = {
        'property': 'reGAP',
        'type': 'categorical',
        'stops': [
            [1, "#26633d"],
            [2, "#879647"],
            [3, "#BBBBBB"],
            [4, "#F8F8F8"]]
        }
paint = {"fill-color": established}

m = leafmap.Map(style="positron")
m.add_gdf(gdf,layer_type="fill", name = "CA 30x30", paint = paint)
m.add_layer_control()
m

Map(height='600px', map_options={'bearing': 0, 'center': (0, 20), 'pitch': 0, 'style': 'https://basemaps.carto…

True